<a href="https://colab.research.google.com/github/hakim3189/MachineLearning/blob/main/Covmo_Coverage_Check.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!nvidia-smi

Mon Feb  3 09:37:48 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   36C    P8              9W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [2]:
!git clone https://github.com/rapidsai/rapidsai-csp-utils.git
!python rapidsai-csp-utils/colab/pip-install.py

Cloning into 'rapidsai-csp-utils'...
remote: Enumerating objects: 567, done.
remote: Counting objects: 100% (298/298), done.
remote: Compressing objects: 100% (196/196), done.
remote: Total 567 (delta 188), reused 144 (delta 100), pack-reused 269 (from 1)
Receiving objects: 100% (567/567), 183.25 KiB | 13.09 MiB/s, done.
Resolving deltas: 100% (290/290), done.
Using Python 3.11.11 environment at /usr
Resolved 2 packages in 65ms
Prepared 2 packages in 7ms
Installed 2 packages in 1ms
 + nvidia-ml-py==12.570.86
 + pynvml==12.0.0
Installing RAPIDS remaining 24.10.* libraries
Using Python 3.11.11 environment at /usr
Resolved 151 packages in 9.66s
Prepared 37 packages in 1m 41s
Uninstalled 10 packages in 251ms
Installed 37 packages in 313ms
 + cucim-cu12==24.10.0
 - cudf-cu12==24.12.0 (from https://pypi.nvidia.com/cudf-cu12/cudf_cu12-24.12.0-cp311-cp311-manylinux_2_24_x86_64.manylinux_2_28_x86_64.whl)
 + cudf-cu12==24.10.1
 + cugraph-cu12==24.10.0
 + cuml-cu12==24.10.0
 + cuproj-cu12==24.10.

In [3]:
import cudf
cudf.__version__

'24.10.01'

In [52]:
!pip install fiona
!pip install contextily
!pip install rioxarray
!pip install xarray-spatial
!pip install gdown
!pip install jupyter_bokeh
!pip install pyogrio

NotImplementedError: A UTF-8 locale is required. Got ANSI_X3.4-1968

In [19]:
import cuxfilter
#%load_ext cudf.pandas
import pandas as pd
from cuxfilter import DataFrame, themes, layouts, charts
from cuxfilter.charts import bokeh
from cuxfilter.charts import datashader
from pathlib import Path
import cudf
import cuml
import datashader as ds
import numpy as np
import geopandas as gpd
import fiona
import cuspatial
from shapely.geometry import Point, Polygon, MultiPolygon
from shapely.geometry import box
import matplotlib.pyplot as plt
import contextily as ctx


%matplotlib inline

import glob
import xarray as xr
import rioxarray

import sys
import xarray as xr
from datashader.transfer_functions import shade
from datashader.transfer_functions import stack
from datashader.transfer_functions import dynspread
from datashader.transfer_functions import set_background
from datashader.colors import Elevation

import xrspatial
from xrspatial import curvature
from xrspatial import hillshade
from xrspatial import slope
from xrspatial.zonal import stats
from xrspatial.classify import equal_interval

import rasterio
import matplotlib.pyplot as plt
from rasterio.plot import show
import gdown

Loading Raw Data

In [20]:
file_id = '1CbSVr6SnBfxL7BPj3VnA7fwcvTcSTgkP' # Replace with the ID from the shareable link
gdown.download(id=file_id, output='Sample_Telco_Data.csv', quiet=False)
df = pd.read_csv('Sample_Telco_Data.csv')
df.head()

Downloading...
From (original): https://drive.google.com/uc?id=1CbSVr6SnBfxL7BPj3VnA7fwcvTcSTgkP
From (redirected): https://drive.google.com/uc?id=1CbSVr6SnBfxL7BPj3VnA7fwcvTcSTgkP&confirm=t&uuid=588433c6-6af6-4890-8585-cee6acd0008b
To: /content/Sample_Telco_Data.csv
100%|██████████| 169M/169M [00:01<00:00, 148MB/s]


Tile Id        Date  Serving Cell Average RSRP (All) (dBm)  \
0  5764608304269632151  2023-09-02                                 -95.45   
1  5764608304267217308  2023-09-02                                -105.29   
2  5764608304271933179  2023-09-02                                -111.00   
3  5764608304270163448  2023-09-02                                 -95.82   
4  5764608304269242660  2023-09-02                                -131.00   

   Serving Cell Average RSRQ (All) (dB) Total MR Count   Longitude  Latitude  
0                                -13.34         15,091  106.993618 -6.312739  
1                                -14.61          4,825  107.065372 -6.351298  
2                                -16.33              6  107.270336 -6.015776  
3                                -12.43         47,579  107.176609 -6.272813  
4                                -20.00              5  107.425861 -6.461840

##### Find data Type

In [21]:
df.dtypes

Tile Id                                    int64
Date                                      object
Serving Cell Average RSRP (All) (dBm)    float64
Serving Cell Average RSRQ (All) (dB)     float64
Total MR Count                            object
Longitude                                float64
Latitude                                 float64
dtype: object

##### Checking why "Total MR Count" as Object, Find non Integer Value in "Total MR Count

In [22]:
non_integer_values = df['Total MR Count'][pd.to_numeric(df['Total MR Count'], errors='coerce').isna()]
print("Non-integer values:", non_integer_values)

Non-integer values: 0          15,091
1           4,825
3          47,579
10          1,500
12         28,160
            ...  
2317979    11,570
2317980     2,219
2317981     2,940
2317982     3,408
2317985    59,469
Name: Total MR Count, Length: 1283881, dtype: object


##### Replacing "," with blank before converting to int32

In [23]:
df['Total MR Count'] = df['Total MR Count'].str.replace(',', '')
df['Date'] = df['Date'].str.replace('-', '')

##### Check again non Integer Value in "Total MR Count"

In [24]:
non_integer_values = df['Total MR Count'][pd.to_numeric(df['Total MR Count'], errors='coerce').isna()]
print("Non-integer values:", non_integer_values)

Non-integer values: Series([], Name: Total MR Count, dtype: object)


##### Check NULL Value Counts

In [25]:
print(df.isnull().sum())

Tile Id                                  0
Date                                     0
Serving Cell Average RSRP (All) (dBm)    0
Serving Cell Average RSRQ (All) (dB)     0
Total MR Count                           0
Longitude                                0
Latitude                                 0
dtype: int64


##### Converting "Total MR Count" from object to Int32

In [26]:
df['Total MR Count'] = df['Total MR Count'].astype(int)

##### Converting "Date" from object to datetime64

In [28]:
df['Date'] = df['Date'].astype('datetime64[ns]')
df.dtypes

Tile Id                                           int64
Date                                     datetime64[ns]
Serving Cell Average RSRP (All) (dBm)           float64
Serving Cell Average RSRQ (All) (dB)            float64
Total MR Count                                    int64
Longitude                                       float64
Latitude                                        float64
dtype: object

##### Check Sample Data

In [29]:
df.head()

Tile Id       Date  Serving Cell Average RSRP (All) (dBm)  \
0  5764608304269632151 2023-09-02                                 -95.45   
1  5764608304267217308 2023-09-02                                -105.29   
2  5764608304271933179 2023-09-02                                -111.00   
3  5764608304270163448 2023-09-02                                 -95.82   
4  5764608304269242660 2023-09-02                                -131.00   

   Serving Cell Average RSRQ (All) (dB)  Total MR Count   Longitude  Latitude  
0                                -13.34           15091  106.993618 -6.312739  
1                                -14.61            4825  107.065372 -6.351298  
2                                -16.33               6  107.270336 -6.015776  
3                                -12.43           47579  107.176609 -6.272813  
4                                -20.00               5  107.425861 -6.461840

Describing The Data

In [32]:
df.describe()


Tile Id                 Date  \
count  2.317986e+06              2317986   
mean   5.764608e+18  2023-09-02 00:00:00   
min    5.764608e+18  2023-09-02 00:00:00   
25%    5.764608e+18  2023-09-02 00:00:00   
50%    5.764608e+18  2023-09-02 00:00:00   
75%    5.764608e+18  2023-09-02 00:00:00   
max    5.764608e+18  2023-09-02 00:00:00   
std    2.642747e+08                  NaN   

       Serving Cell Average RSRP (All) (dBm)  \
count                           2.317986e+06   
mean                           -1.060013e+02   
min                            -1.410000e+02   
25%                            -1.106600e+02   
50%                            -1.055300e+02   
75%                            -1.008500e+02   
max                            -4.889000e+01   
std                             7.477592e+00   

       Serving Cell Average RSRQ (All) (dB)  Total MR Count     Longitude  \
count                          2.317986e+06    2.317986e+06  2.317986e+06   
mean                          -1.400060e+01    2.904748e+04  1.072199e+02   
min                           -2.000000e+01    0.000000e+00  1.065075e+02   
25%                           -1.513000e+01    1.870000e+02  1.070801e+02   
50%                           -1.374000e+01    1.537000e+03  1.072123e+02   
75%                           -1.264000e+01    1.380900e+04  1.073575e+02   
max                           -3.000000e+00    4.630699e+07  1.077201e+02   
std                            2.031192e+00    1.803351e+05  1.789649e-01   

           Latitude  
count  2.317986e+06  
mean  -6.248577e+00  
min   -6.654889e+00  
25%   -6.353345e+00  
50%   -6.252336e+00  
75%   -6.151307e+00  
max   -5.920508e+00  
std    1.355919e-01

In [33]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2317986 entries, 0 to 2317985
Data columns (total 7 columns):
 #   Column                                 Dtype         
---  ------                                 -----         
 0   Tile Id                                int64         
 1   Date                                   datetime64[ns]
 2   Serving Cell Average RSRP (All) (dBm)  float64       
 3   Serving Cell Average RSRQ (All) (dB)   float64       
 4   Total MR Count                         int64         
 5   Longitude                              float64       
 6   Latitude                               float64       
dtypes: datetime64[ns](1), float64(4), int64(2)
memory usage: 123.8 MB


##### Adding Mercator Long lat Format based on Longitude Latitude Data

In [35]:
df['x'], df['y'] = ds.utils.lnglat_to_meters(df['Longitude'], df['Latitude'])

##### Converting Pandas dataframe to CuDF dataframe

In [36]:
cu_df = cudf.from_pandas(df)

##### Adding CuDF Dataframe to CuXFilter Dataframe

In [37]:
cux_df = cuxfilter.DataFrame.from_dataframe(cu_df)

##### Preparing Color Palette

In [38]:
gtc_demo_red_blue_palette = [ "#3182bd", "#6baed6", "#7b8ed8", "#e26798", "#ff0068" , "#323232" ]

##### Creating Mapping Chart

In [39]:
chart1 = cuxfilter.charts.scatter(x='x', y='y', aggregate_col='Serving Cell Average RSRP (All) (dBm)', aggregate_fn='mean',
                                color_palette=gtc_demo_red_blue_palette,tile_provider="OSM",  unselected_alpha=0.2,
                                pixel_shade_type='linear')

##### Creating CuXFilter Dashboard

In [42]:
d = cux_df.dashboard([chart1], title='RSRP Map')

##### Launching CuxFilter Dashboard

In [43]:
d.app()

GridSpec(ncols=12, nrows=1)
    [0] GridSpec(height=800, ncols=12, nrows=5, sizing_mode='fixed', width=1200)
        [0] HoloViews(DynamicMap, height=800, sizing_mode='stretch_both', width=1200)
    [1] WidgetBox(styles={'border-color': '...})
        [0] Number(css_classes=['indicator'], default_color='#2B2B2B', font_size='18pt', format='{value:,}', name='Datapoints Selected', sizing_mode='stretch_width', title_size='14pt', value=2317986)
        [1] Progress(sizing_mode='stretch_width', styles={'--success-bg-color': '...}, value=100)

### Customize Mapping

##### Make new color Palette for new Legend

In [44]:
RSRP_Palete = [ "#3d31bd", "#0da60a", "#02f73c", "#f6fa02", "#fa0202" ]

##### Group RSRP value Based on current telco standard

In [45]:
df['RSRP_Status'] = np.select(
    [
        (df['Serving Cell Average RSRP (All) (dBm)'] >= -80),
        (df['Serving Cell Average RSRP (All) (dBm)'] >= -95) & (df['Serving Cell Average RSRP (All) (dBm)'] < -80),
        (df['Serving Cell Average RSRP (All) (dBm)'] >= -100) & (df['Serving Cell Average RSRP (All) (dBm)'] < -95),
        (df['Serving Cell Average RSRP (All) (dBm)'] >= -110) & (df['Serving Cell Average RSRP (All) (dBm)'] < -100),
        (df['Serving Cell Average RSRP (All) (dBm)'] >= -150) & (df['Serving Cell Average RSRP (All) (dBm)'] < -110)
        # Add more conditions as needed
    ],
    [
        1,
        2,
        3,
        4,
        5
        # Add corresponding values for each condition
    ],
    default='Other'
)

##### Check current dtypes

In [46]:
df.dtypes

Tile Id                                           int64
Date                                     datetime64[ns]
Serving Cell Average RSRP (All) (dBm)           float64
Serving Cell Average RSRQ (All) (dB)            float64
Total MR Count                                    int64
Longitude                                       float64
Latitude                                        float64
x                                               float64
y                                               float64
RSRP_Status                                      object
dtype: object

###### Coverting RSRP_Status to Integer

In [47]:
df['RSRP_Status'] = df['RSRP_Status'].astype(int)
df.dtypes

Tile Id                                           int64
Date                                     datetime64[ns]
Serving Cell Average RSRP (All) (dBm)           float64
Serving Cell Average RSRQ (All) (dB)            float64
Total MR Count                                    int64
Longitude                                       float64
Latitude                                        float64
x                                               float64
y                                               float64
RSRP_Status                                       int64
dtype: object

#### Adding Region Data Map

##### Check Driver support for Mapinfo Data

In [48]:
print('MapInfo File' in fiona.supported_drivers)

True


##### Loading Tab File Data

In [50]:
file_id = '1zwV4MNriXV4ArUZ6Y8I3pCoVYiRhM87W' # Replace with the ID from the shareable link
gdown.download(id=file_id, output='BTS_KABUPATEN_NASIONAL_V20.TAB', quiet=False)
tab_data = gpd.read_file("BTS_KABUPATEN_NASIONAL_V20.TAB", driver='MapInfo File') # Explicitly specify the driver

Downloading...
From: https://drive.google.com/uc?id=1zwV4MNriXV4ArUZ6Y8I3pCoVYiRhM87W
To: /content/BTS_KABUPATEN_NASIONAL_V20.TAB
100%|██████████| 602/602 [00:00<00:00, 1.18MB/s]


DataSourceError: 'BTS_KABUPATEN_NASIONAL_V20.TAB' not recognized as being in a supported file format. It might help to specify the correct driver explicitly by prefixing the file path with '<DRIVER>:', e.g. 'CSV:path'.